# De novo design

### Developers: Mat Bieniek, Ben Cree, Rachael Pirie, Josh Horton

* Add R-groups in user-defined positions
* Output ADMET properties
* Perform constrained optimisation
* Score poses
* Send output to free energy calculations

Open source, customisable, fast/easy to use.

In [6]:
import copy
import glob
%cd ~/rgroups/temp/rgroups
import prody
from rdkit import Chem
from rdkit.Chem import Draw

from rgroup import RMol, RList, build_molecules, fix_receptor, optimise_in_receptor, RGroups, sort_conformers, ic50

/home/c0065492/rgroups/temp/rgroups


<frozen importlib._bootstrap>:228: RuntimeWarning: to-Python converter for boost::shared_ptr<RDKit::FilterCatalogEntry const> already registered; second conversion method ignored.


In [8]:
%cd ~/rgroups/rgroups/tyk2

[Errno 2] No such file or directory: '/home/c0065492/rgroups/rgroups/tyk2'
/home/c0065492/rgroups/temp/rgroups


In [ ]:
!wget -nc https://files.rcsb.org/download/4HW2.pdb
pdb = '4HW2.pdb'

In [ ]:
# RMol.set_gnina(loc='/home/c0065492/rgroups/rgroups/gnina')

In [5]:
# load the complex with the ligand
sys = prody.parsePDB(pdb)
#sys = prody.parsePDB('jnk1/2gmx.pdb')

rec = sys.select('not (nucleic or hetatm) and not water')
mol = sys.select('resname XEY')
#mol = sys.select('resname 877')

prody.writePDB('rec.pdb', rec)
#prody.writePDB('lig.pdb', mol)

@> 7376 atoms and 1 coordinate set(s) were parsed in 0.06s.


'rec.pdb'

In [6]:
#!wget 'https://models.rcsb.org/v1/5nev/ligand?auth_seq_id=301&label_asym_id=E&encoding=sdf&filename=5nev_E_72L.sdf' -O lig.sdf
#!obabel jnk1/core.sdf -O jnk1/coreh.sdf -p 7
!obabel -isdf core.sdf -osdf -O coreh.sdf -p 7
# ^manually modify the files if need be

1 molecule converted


In [7]:
# load the ligand
# rdkit doesn't do a good job with protonation, 
#init_mol = Chem.MolFromPDBFile('lig.pdb', removeHs=False)
#init_mol = Chem.AddHs(init_mol, addCoords=True)

init_mol = Chem.SDMolSupplier('coreh.sdf', removeHs=False)[0]

# get the R group representation of the rdkit Mol
rinit_mol = RMol(init_mol)

In [8]:
# select the atom to be replaced with the R group
rinit_mol.rep2D(idx=True, size=(500, 500))

In [9]:
# look up r groups and select
RGroups #still dont know how to use this GUIipyn

In [10]:
ligand_ids = [27, 28, 31, 42, 43, 44, 45, 46, 47, 48, 49, 50, 54, 55]
# read the rgroups 1 by 1 in a loop
# assumes that there is only one -r.mol in each dir
rgroups = [Chem.MolFromMolFile(glob.glob(f'{ligand_id}/*-r.mol')[0], removeHs=False) for ligand_id in ligand_ids]
rgroups

In [11]:
ligand_ids[7] #to check what rgroup is failing optimisation or clash with protein

46

In [12]:
# build a list of molecules
attachment_index = [28]
rmols = build_molecules(rinit_mol, attachment_index, rgroups)

Rgroup atom index <rdkit.Chem.rdchem.QueryAtom object at 0x7fabdc470100> neighbouring <rdkit.Chem.rdchem.Atom object at 0x7fabdc470880>
Rgroup atom index <rdkit.Chem.rdchem.QueryAtom object at 0x7fabdc470340> neighbouring <rdkit.Chem.rdchem.Atom object at 0x7fabdc470280>
Rgroup atom index <rdkit.Chem.rdchem.QueryAtom object at 0x7fabdc470100> neighbouring <rdkit.Chem.rdchem.Atom object at 0x7fabdc470880>
Rgroup atom index <rdkit.Chem.rdchem.QueryAtom object at 0x7fabdc470340> neighbouring <rdkit.Chem.rdchem.Atom object at 0x7fabdc470280>
Rgroup atom index <rdkit.Chem.rdchem.QueryAtom object at 0x7fabdc470880> neighbouring <rdkit.Chem.rdchem.Atom object at 0x7fabdc470100>
Rgroup atom index <rdkit.Chem.rdchem.QueryAtom object at 0x7fabdc470340> neighbouring <rdkit.Chem.rdchem.Atom object at 0x7fabdc470280>
Rgroup atom index <rdkit.Chem.rdchem.QueryAtom object at 0x7fabdc470880> neighbouring <rdkit.Chem.rdchem.Atom object at 0x7fabdc470100>
Rgroup atom index <rdkit.Chem.rdchem.QueryAtom o

In [13]:
rmols.rep2D()

In [14]:
rmols[9].rep3D()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [15]:
rmols.toxicity()

MW  HBA  HBD    LogP  Pass_Ro5  has_pains  has_unwanted_subs  \
0  382.999510    3    2  4.2065      True      False               True   
0  363.054132    3    2  4.2352      True      False              False   
0  323.022832    3    2  3.5991      True      False              False   
0  337.038482    3    2  3.9892      True      False              False   
0  351.054132    3    2  4.2352      True      False              False   
0  365.069782    3    2  4.6253      True      False              False   
0  363.054132    3    2  4.3793      True      False              False   
0  349.038482    3    2  3.9892      True      False              False   
0  363.054132    3    2  4.3793      True      False              False   
0  377.069782    3    2  4.7694      True      False              False   
0  385.038482    3    2  4.8930      True      False              False   
0  339.017747    4    3  2.5715      True      False              False   
0  352.049381    3    3  3.7821      True      False              False   
0  339.017747    4    2  3.8190      True      False              False   

   has_prob_fgs  synthetic_accessibility  
0          True                 7.550787  
0         False                 7.964912  
0         False                 6.747622  
0         False                 7.010544  
0         False                 7.250500  
0         False                 7.456506  
0         False                 7.269905  
0         False                 7.031819  
0         False                 7.305428  
0         False                 7.523953  
0         False                 6.985585  
0         False                 6.801717  
0         False                 7.162721  
0         False                 6.705513

In [16]:
rmols.generate_conformers(num_conf=50, 
                         minimum_conf_rms=0.5 
                         )

RMol 1
removed 40 duplicated conformations
RMol 2
removed 30 duplicated conformations
RMol 3
removed 48 duplicated conformations
RMol 4
removed 42 duplicated conformations
RMol 5
removed 26 duplicated conformations
RMol 6
removed 7 duplicated conformations
RMol 7
removed 31 duplicated conformations
RMol 8
removed 39 duplicated conformations
RMol 9
removed 35 duplicated conformations
RMol 10
removed 26 duplicated conformations
RMol 11
removed 49 duplicated conformations
RMol 12
removed 45 duplicated conformations
RMol 13
removed 38 duplicated conformations
RMol 14
removed 47 duplicated conformations


In [17]:
#rmol.rep3D(template=True)

In [18]:
rmols.GetNumConformers()

[11, 21, 3, 9, 25, 44, 20, 12, 16, 25, 2, 6, 13, 4]

### Optimise conformers in context of protein

In [19]:
# fix the receptor file 
fix_receptor("rec.pdb", "rec_h.pdb")
# load back into prody
rec_fix = prody.parsePDB("rec_h.pdb")

@> 14571 atoms and 1 coordinate set(s) were parsed in 0.09s.


In [20]:
# filter by the protein clashes
rmols[0].rep3D(prody=rec_fix)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [21]:
rmols.removeConfsClashingWithProdyProt(rec_fix)

RMol 1
RMol 2
RMol 3
RMol 4
RMol 5
RMol 6
RMol 7
RMol 8
RMol 9
RMol 10
RMol 11
RMol 12
RMol 13
RMol 14


In [22]:
rmols[0].rep3D(prody=rec_fix)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [23]:
# opt_mol, energies
energies = rmols.optimise_in_receptor(
    receptor_file="rec_h.pdb", 
    ligand_force_field="openff", 
    use_ani=True,
    sigma_scale_factor=0.8,
    relative_permittivity=4
)

Warning (not error because allow_undefined_stereo=True): Unable to make OFFMol from RDMol: RDMol has unspecified stereochemistry. RDMol name: 0X5Undefined chiral centers are:
 - Atom C (index 28)
 - Atom C (index 30)



RMol 1


Warning (not error because allow_undefined_stereo=True): Unable to make OFFMol from RDMol: RDMol has unspecified stereochemistry. Undefined chiral centers are:
 - Atom C (index 11)
 - Atom C (index 16)

Warning (not error because allow_undefined_stereo=True): Unable to make OFFMol from RDMol: RDMol has unspecified stereochemistry. Undefined chiral centers are:
 - Atom C (index 8)
 - Atom C (index 13)

Warning (not error because allow_undefined_stereo=True): Unable to make OFFMol from RDMol: RDMol has unspecified stereochemistry. Undefined chiral centers are:
 - Atom C (index 11)
 - Atom C (index 16)

Warning (not error because allow_undefined_stereo=True): Unable to make OFFMol from RDMol: RDMol has unspecified stereochemistry. Undefined chiral centers are:
 - Atom C (index 8)
 - Atom C (index 13)



using ani2x


Optimising conformer: 100%|█████████████████████| 11/11 [02:47<00:00, 15.21s/it]


...

Optimising conformer: 100%|█████████████████████| 13/13 [03:11<00:00, 14.74s/it]


RMol 14


Warning (not error because allow_undefined_stereo=True): Unable to make OFFMol from RDMol: RDMol has unspecified stereochemistry. Undefined chiral centers are:
 - Atom C (index 11)
 - Atom C (index 16)



using ani2x


Optimising conformer: 100%|███████████████████████| 4/4 [01:05<00:00, 16.43s/it]


In [24]:
rmols[0].rep3D()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [25]:
for i in range(len(ligand_ids)):
    rmols[i].to_file("optimised_coords_" + str(ligand_ids[i]) + ".pdb")

In [26]:
print(energies)

[[-852316.8154879261, -852319.3923676129, -852318.6973807226, -852320.2627865318, -852318.6098833503, -852317.6590029623, -852320.2883913302, -852319.5210968464, -852321.3747548928, -852317.9542134546, -852320.1438354055], [-588589.7528619964, -588594.1885725417, -588593.2388166522, -588591.8807586711, -588592.116522844, -588591.7167716902, -588593.1260469238, -588592.4773729467, -588591.3543310324, -588593.8806235832, -588593.2365660552, -588591.1879948115, -588593.8799650193, -588591.359950848, -588591.7127897084, -588592.4768781805, -588591.8802514632, -588591.1884171866, -588593.1242614377, -588594.1881096964, -588591.8805386899], [-515390.98182398453, -515391.3241151743, -515391.3248459349], [-540034.2200620412, -540034.150128503, -540034.1500159911, -540033.4962946419, -540033.4957727628, -540033.4958831627, -540034.1498195825, -540033.4963563451, -540033.4965446288], [-564700.862145223, -564699.4776091219, -564699.801966957, -564699.4769636273, -564699.8012089876, -564699.802395

In [27]:
final_energies = rmols.sort_conformers(energy_range=5)

RMol 1
RMol 2
RMol 3
RMol 4
RMol 5
RMol 6
RMol 7
RMol 8
RMol 9
RMol 10
RMol 11
RMol 12
RMol 13
RMol 14


In [28]:
len(ligand_ids) == len(rmols) #check theyre equal or very bad and silent things happen

True

In [29]:
for i in range(len(ligand_ids)):
    rmols[i].to_file("best_conformers_" + str(ligand_ids[i]) + ".pdb")

In [30]:
print(final_energies)

[[0.0, 1.0863635626155883, 1.1119683609576896, 1.2309194873087108, 1.8536580463405699, 1.9823872798588127, 2.6773741701617837, 2.7648715424584225, 3.42054143815767, 3.715751930489205, 4.559266966651194], [0.0, 0.00046284531708806753, 0.3079489584779367, 0.3086075223982334, 0.9497558894800022, 0.9520064864773303, 1.06252561789006, 1.064311104011722, 1.7111995950108394, 1.7116943611763418, 2.07204969774466, 2.30781387060415, 2.308033851790242, 2.3083210785407573, 2.4718008515192196, 2.475782833294943, 2.828621693653986, 2.8342415093211457, 3.000155355082825, 3.0005777302430943, 4.435710545280017], [0.0, 0.0007307606283575296, 0.3430219503934495], [0.0, 0.06993353820871562, 0.0700460501248017, 0.07024245872162282, 0.7235174124361947, 0.7237056960584596, 0.7237673993222415, 0.7241788784740493, 0.7242892783833668], [0.0, 1.059720793622546, 1.0597492658998817, 1.0599974534707144, 1.0600267745321617, 1.0600626937812194, 1.0601782659068704, 1.0604293699143454, 1.0604335549287498, 1.06050798390

In [ ]:
CNNscores = rmols.gnina(receptor_file="rec_h.pdb") 
CNNscores

RMol 1
Gnina not found or set. Download gnina (~500MB) into /home/c0065492/rgroups/rgroups/tyk2
RMol 2
RMol 3
RMol 4
RMol 5
RMol 6
RMol 7
RMol 8
RMol 9
RMol 10
RMol 11
RMol 12
RMol 13


In [ ]:
ic50_scores = []
for i in range(len(CNNscores)):
    ic50_scores.append([ic50(x) for x in CNNscores[i]])

In [ ]:
ic50_scores

In [ ]:
for i in range(len(ic50_scores)):
    with open('scores_' + str(ligand_ids[i]) + '.dat', 'w') as f:
        for x in range(len(ic50_scores[i])):
            f.write(str(ic50_scores[i][x])+'\n')

In [ ]:
lowest = []
for i in range(len(ic50_scores)):
    lowest.append(ic50_scores[i][0])

In [ ]:
lowest #lowest gnina values in nM

In [ ]:
#expt = [5.1, 8.5, 96, 64, 840, 3500, 94, 4.8, 74, 240, 2000, 250, 18, 170] #expt values in nm
expt = [35000, 15000, 8800, 1900, 1700, 16000, 9800, 9900, 380, 1100]

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
fig=plt.figure()
ax=fig.add_axes([0,0,1,1])
ax.scatter(expt, lowest, color='black', marker='x')
ax.set_xlabel('Experimental IC50 / nM')
ax.set_ylabel('Gnina IC50 / nM')
plt.show()